In [1]:
import pandas as pd
import pickle
from tqdm import tqdm
from glob import glob
import re

In [2]:
import cufflinks as cf
cf.go_offline()

In [3]:
data_filenames = glob('data_room/*')

In [4]:
data = []
for fn in tqdm(data_filenames):
    with open(fn, 'rb') as f:
        data.extend(pickle.load(f)) 

100%|██████████| 53/53 [00:01<00:00, 27.80it/s]


## EDA

### 전세와 월세

In [8]:
room_info = pd.read_csv('data_preprocessed/room_info_221002.csv')

In [9]:
room_info['sales_type'].unique()

array(['월세', '전세'], dtype=object)

In [12]:
count_by_gu = room_info.groupby('local2').size()  # 구별 매물 비율
monthly_ratio = room_info.groupby('local2').apply(lambda x:sum(x['sales_type'] == '월세')/len(x))  # 구별 월세 비율

In [13]:
count_by_gu = count_by_gu.sort_values().reset_index()

In [14]:
count_by_gu.columns = ['local2', 'value']

In [15]:
count_by_gu.iplot(kind='pie', labels='local2', values='value', title='서울 구별 매물 비율')

In [97]:
monthly_ratio.sort_values().iplot(kind='bar', title="서울 구별 월세 비율")

In [165]:
room_charter = room_info[room_info['sales_type'] == '전세']

In [166]:
room_monthly = room_info[room_info['sales_type'] == '월세']

In [146]:
room_monthly[room_monthly['보증금액']< 30000]['보증금액'].iplot(kind='hist')

In [114]:
room_monthly['월세금액'].sort_values()

10730         2.0
11307         2.0
18824         3.0
18849         3.0
1517          3.0
           ...   
17027       650.0
10158       750.0
10010       960.0
14185      1200.0
16592    950000.0
Name: 월세금액, Length: 12966, dtype: float64

In [121]:
room_monthly['월세금액'].astype(int)

0        130
2        200
3        165
9        150
10       120
        ... 
26160    140
26161     75
26162     90
26163     30
26164     60
Name: 월세금액, Length: 12966, dtype: int32

In [144]:
room_monthly[room_monthly['월세금액']< 500]['월세금액'].iplot(kind='hist')

In [167]:
gwan = room_monthly[room_monthly['local2'] == '관악구']

In [168]:
gwan[gwan['전용면적_m2'] < 20]

item_id   user_no sales_type  보증금액  월세금액  전용면적_m2  공급면적_m2 local1  \
18355  33448364   8284053         월세   100  15.0    19.83    19.83    서울시   
18356  33484852     73823         월세   100  25.0    16.53    16.53    서울시   
18357  33443963  13141992         월세    50  20.0    19.83    19.83    서울시   
18358  33451789  17849486         월세   200  20.0    19.83    19.83    서울시   
18359  33474609   5896403         월세   100  15.0    19.83    19.83    서울시   
...         ...       ...        ...   ...   ...      ...      ...    ...   
24429  33486597   5219251         월세  1000  35.0    17.48    17.48    서울시   
24466  33442892  12748538         월세   100  28.0    16.53    16.53    서울시   
24467  33482405   5725862         월세  1000  49.0    19.83    19.83    서울시   
24487  33414693   8284053         월세   100  23.0    16.53    16.53    서울시   
24488  33474510   5219251         월세  5000  35.0    12.15    12.15    서울시   

      local2 local3                        random_location floor  \
18355    관악구    신림동   37.47283517182575,126.93807149178181     1   
18356    관악구    신림동   37.472606855599444,126.9418290881236     3   
18357    관악구    신림동   37.47204393648989,126.93975780983754     2   
18358    관악구    신림동   37.47203392135477,126.93993318386845     3   
18359    관악구    신림동   37.47033923441222,126.93729143126326     5   
...      ...    ...                                    ...   ...   
24429    관악구    신림동    37.4813012060367,126.90363618352035     2   
24466    관악구    신림동   37.48129916920792,126.90198336529974     3   
24467    관악구    신림동    37.48005086500832,126.9000457764886     3   
24487    관악구    신림동  37.481782702027935,126.90198323931259     3   
24488    관악구    신림동    37.4803691536494,126.90167239365941     6   

                updated_at approve_date residence_type  
18355  2022-09-21 18:48:59   2007-01-30            사무소  
18356  2022-09-24 16:12:34   2007-10-16      제2종근린생활시설  
18357  2022-09-21 15:30:37   2001-05-22         근린생활시설  
18358  2022-09-22 10:54:17     20060809      2종 근린생활시설  
18359  2022-09-23 17:09:17   2003-02-26         근린생활시설  
...                    ...          ...            ...  
24429  2022-09-24 18:10:09     20171120           다중주택  
24466  2022-09-21 14:49:07     19770627             주택  
24467  2022-09-24 13:40:45   2020.07.03         근린생활시설  
24487  2022-09-19 16:38:49     19770627             주택  
24488  2022-09-23 17:05:52     20140325             도생  

[739 rows x 15 columns]

In [56]:
import plotly.express as px
fig = px.scatter_mapbox(room_info[room_info['approve_year'] > 1979], lat="random_lat", lon="random_long",
                         zoom=10, height=500, color='approve_year', opacity=0.3)
fig.update_layout(mapbox_style="carto-positron")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

## 지하철역과의 거리

## 전용면적과 월세

## 전용면적과 월세

## 전세/월세가 싼 지역

In [13]:
room_info['random_lat']

0        37.559750
1        37.558609
2        37.558575
3        37.560500
4        37.553005
           ...    
26160    37.555112
26161    37.554190
26162    37.561877
26163    37.563031
26164    37.553483
Name: random_lat, Length: 26165, dtype: float64

In [14]:
room_info

item_id   user_no sales_type   보증금액   월세금액  전용면적_m2  공급면적_m2 local1  \
0      33446567   5987034         월세   2000  130.0    52.69    57.70    서울시   
1      33203240    322799         전세  55000    NaN    29.29    39.67    서울시   
2      33181218   8485448         월세   5000  200.0    39.08    59.00    서울시   
3      33459584   5987034         월세   3000  165.0    72.73    79.34    서울시   
4      32955508  17675823         전세  35000    NaN    29.75    39.67    서울시   
...         ...       ...        ...    ...    ...      ...      ...    ...   
26160  33347615   5748503         월세   1000  140.0    50.45    50.45    서울시   
26161  33442975     37495         월세   1000   75.0    30.08    30.08    서울시   
26162  33452271    325211         월세   1000   90.0    26.45    26.45    서울시   
26163  33346230   6017035         월세    300   30.0    11.57    11.57    서울시   
26164  33467478    169251         월세   5500   60.0    33.06    36.36    서울시   

      local2 local3                        random_location floor  \
0       서대문구    창천동   37.55975011593247,126.93329296545063     1   
1       서대문구    창천동   37.55860942977413,126.92758585174795   NaN   
2       서대문구    창천동   37.55857456629137,126.92824978616616     5   
3        마포구    연남동   37.56050038416363,126.91826753775781     2   
4        마포구    창전동   37.55300474509232,126.92640419917751     2   
...      ...    ...                                    ...   ...   
26160    마포구   노고산동  37.555112040570464,126.93372237850967     5   
26161    마포구    서교동   37.55418960217351,126.92495843795764     3   
26162    마포구    연남동   37.56187727651494,126.92655784969199     3   
26163   서대문구    연희동  37.563030855760196,126.92974609481554     3   
26164    마포구    창전동    37.5534828402926,126.92845603646984   반지하   

                updated_at approve_date    residence_type  approve_year  \
0      2022-09-21 17:21:02   1990.01.16             다세대주택          1990   
1      2022-09-15 14:04:27   2022.07.08             다세대주택          2022   
2      2022-09-14 15:12:46  2022-07-08               오피스텔          2022   
3      2022-09-22 16:21:05  1993-10-06          다가구용 단독주택          1993   
4      2022-09-01 21:22:07     20190820         제2종근린생활시설          2019   
...                    ...          ...               ...           ...   
26160  2022-09-14 13:49:36  2022-06-13   다세대주택,업무시설(오피스텔)          2022   
26161  2022-09-22 18:18:41    2002.8.24             다가구주택          2002   
26162  2022-09-22 11:08:51     20150317              단독주택          2015   
26163  2022-09-14 12:46:20     20010523              단독주택          2001   
26164  2022-09-23 11:46:12     19881224              단독주택          1988   

       random_lat  random_long  is_underground  
0       37.559750   126.933293               0  
1       37.558609   126.927586               0  
2       37.558575   126.928250               0  
3       37.560500   126.918268               0  
4       37.553005   126.926404               0  
...           ...          ...             ...  
26160   37.555112   126.933722               0  
26161   37.554190   126.924958               0  
26162   37.561877   126.926558               0  
26163   37.563031   126.929746               0  
26164   37.553483   126.928456               1  

[26165 rows x 19 columns]

In [ ]:
import plotly.express as px
fig = px.density_mapbox(room_info, lat='random_lat', lon='random_long', z='월세금액', radius=10,
                        center=dict(lat=37, lon=126), zoom=11,
                        mapbox_style="stamen-terrain")
fig.show()

In [55]:
import plotly.express as px
fig = px.scatter_mapbox(room_info[room_info['approve_year'] > 1979], lat="random_lat", lon="random_long",
                         zoom=10, height=500, color='approve_year', opacity=0.3)
fig.update_layout(mapbox_style="carto-positron")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

## 전세가 강세인 지역